# HW2 Naive Bayes classifier

Create a Naive Bayes classifier for each handwritten digit that support discrete and continuous features.

Function:

1. In Discrete mode:

Tally the frequency of the values of each pixel into 32 bins. For example, The gray
level 0 to 7 should be classified to bin 0, gray level 8 to 15 should be bin 1 ... etc.
Then perform Naive Bayes classifier. Note that to avoid empty bin, you can use
a peudocount (such as the minimum value in other bins) for instead.

2. In Continuous mode:

Use MLE to fit a Gaussian distribution for the value of each pixel. Perform Naive
Bayes classifier.
Sample input & output (for

# Deal with data

https://notebook.community/WNoxchi/Kaukasos/research/idx-to-numpy

In [16]:
import struct
import gzip
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

def read_IDX(fname):
    with gzip.open(fname) as f:
        zero, data_type, dims = struct.unpack('>HBB', f.read(4))
        shape = tuple(struct.unpack('>I', f.read(4))[0] for d in range(dims))
        return np.frombuffer(f.read(), dtype=np.uint8).reshape(shape)
def pic_reshape(matrix):
    d = matrix.shape[0]
    dd = matrix.shape[1]
    ddd = matrix.shape[2]
    matrix = matrix.reshape((d,dd*ddd))
    return matrix

In [17]:
train_image = read_IDX('train-images-idx3-ubyte.gz')
train_label = read_IDX('train-labels-idx1-ubyte.gz')
test_image = read_IDX('t10k-images-idx3-ubyte.gz')
test_label = read_IDX('t10k-labels-idx1-ubyte.gz')

In [18]:
print(train_image.shape)
print(test_image.shape)
train_image = pic_reshape(train_image)
test_image = pic_reshape(test_image)
train_label = train_label.reshape(len(train_label))
test_label= test_label.reshape(len(test_label))

print(train_image.shape)
print(test_image.shape)
print(train_label.shape)
print(test_label.shape)

(60000, 28, 28)
(10000, 28, 28)
(60000, 784)
(10000, 784)
(60000,)
(10000,)


In [19]:
print(test_label)

[7 2 1 ... 4 5 6]


In [20]:
# Get prior, calculate the possibility of ever y

def prior(label):
    prior = np.zeros(10)
    for i in range(10):
        prior[i] = np.sum(label ==i)/len(label)
    return prior

In [21]:
# print out

def print_imagination_numbers(post,threshold):
    print('Imagination of numbers in Bayesian classifier:')
    for l in range(10):
        print('{}:'.format(l))
        for i in range(28):
            for j in range(28):
                if np.argmax(post[l,i*28+j])>=threshold:
                    print('1',end=' ')
                else:
                    print('0',end=' ')
            print()
        print()
    print()

# Discrete

In [22]:
# Classify every pixel into 32 classes
# x = train_image, y = train_label

def pixel_class_discrete(x, y):
    ans = np.zeros((10, 28*28, 32))
    for i in range(len(x)):
        label = y[i]
        for j in range(28*28):
            ans[label][j][np.int(x[i, j])//8] += 1

    # normalization
    for l in range(10):
        for p in range(28*28):
            count = 0
            for c in range(32):
                count += ans[l][p][c]
            ans[l][p][:] /= count
    return ans


def discrete_predict( x, y, test_length, pixel, prior):
    error = 0
    for i in range(test_length):
        post = np.zeros(10)
        # calculate posterior probability
        for l in range(10):
            for p in range(28 * 28):
                post[l] += np.log(max(1e-4, pixel[l, p, int(x[i, p])//8]))
            post[l] += np.log(prior[l])
        
        # probability is negative
        post /= np.sum(post)
        print('Posterior (in log scale):')
        for k in range(10):
            print('{}: {}'.format(k, post[k]))
        predict = np.argmin(post)
        # 為何取最小?
        print('Prediction: {}, Ans: {}'.format(predict, y[i]))
        print()
        if predict != y[i]:
            error += 1
    print('Error rate: {:.4f}'.format(error / test_length))
    print()

# Continuous

In [23]:
import math

# some formula for mu and variance


def mu(data):
    return np.mean(data)


def variance(data, back_var):
    var = np.var(data)
    # Gaussian can't be divided by 0
    if var != 0:
        return var
    else:
        return back_var


def gaussain(data, mean, var):
    #one = (1/math.sqrt(2*math.pi*var))
    #e = math.exp((-(data - mean**2)/(2*var)))
    #ans = one*e
    return ((1/math.sqrt(2*math.pi*var))*math.exp((-(data-mean)**2)/(2*var)))


def pixel_post_continuous(x, y, back_var):
    ans = np.zeros((10, 28*28, 256))
    # 256:每個 pixel會有 255個值
    for l in range(10):  
        pixels = x[y == l]
        for p in range(28*28):
            mean = mu(pixels[:, p])
            var = variance(pixels[:, p], back_var)
            for i in range(256):
                ans[l, p, i] = gaussain(i, mean, var)
    return ans


def continuous_predict(x, y, length, pixel, prior_value, back_prob):
    error = 0
    for i in range(length):
        post = np.zeros(10)
        for l in range(10):
            
            for d in range(28 * 28):  
                post[l] += np.log(max(back_prob,
                                   pixel[l, d, int(x[i, d])]))
            post[l] += np.log(prior_value[l])
        # normalized
        post /= np.sum(post)
        print('Posterior (in log scale):')
        for l in range(10):
            print('{}: {}'.format(l, post[l]))
        predict = np.argmin(post) # select the smallest
        print('Prediction: {}, Ans: {}'.format(predict, y[i]))
        print()
        if predict != y[i]:
            error += 1
    print('Error rate: {:.4f}'.format(error / length))
    print()
    

In [24]:
# Naive Bayesian main
#import sys

def NB_main(toggle, train_x, train_y,test_x,test_y):
    n = len(test_y)
    if toggle == 0:
        discrete_prob = pixel_class_discrete(train_x, train_y)
        prior_d = prior(train_y)
        discrete_predict(test_x,test_y, n, discrete_prob, prior_d)
        print_imagination_numbers(discrete_prob,16)        
    else:
        back_var = 20 # should be large
        back_prob = 1e-50 # should be small
        continuous_prob = pixel_post_continuous(train_x, train_y, back_var)
        prior_c = prior(train_y)
        #print('back_var:{},back_prob:{}'.format(back_var,back_prob))
        continuous_predict(test_x,test_y, n ,continuous_prob ,prior_c,back_prob)
        print_imagination_numbers(continuous_prob,128)

In [25]:
NB_main(0, train_image,train_label,test_image,test_label)

Posterior (in log scale):
0: 0.1110584212873467
1: 0.11929719805351668
2: 0.10525595784545189
3: 0.09983411223879049
4: 0.09361420155207421
5: 0.09722267631166763
6: 0.11526582213409427
7: 0.07376552288489126
8: 0.09924652479526214
9: 0.08543956289690467
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.09988996532166798
1: 0.10792179037615664
2: 0.08243998312252636
3: 0.09002300610224136
4: 0.10882780253980255
5: 0.09224200977015605
6: 0.08926034360405265
7: 0.11975803611946034
8: 0.09623471147551221
9: 0.11340235156842386
Prediction: 2, Ans: 2

Posterior (in log scale):
0: 0.12889085354292049
1: 0.06352669088735036
2: 0.09849136260738496
3: 0.10048811529680136
4: 0.1033613335207858
5: 0.09645494085909011
6: 0.1033266618190807
7: 0.10204913879392363
8: 0.10019127545579212
9: 0.10321962721687047
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.07721987241226218
1: 0.1434729126442954
2: 0.09661180896171435
3: 0.09609972378963001
4: 0.10124855915672577
5: 0.0922192353903342
6: 0

6: 0.10819647898367127
7: 0.07804750161782228
8: 0.09947624546983151
9: 0.08731739883428256
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.13321480875580904
1: 0.07046623262116107
2: 0.10667688196041583
3: 0.09908783207051768
4: 0.10156250526777272
5: 0.09388830108744049
6: 0.1042199443394096
7: 0.09638073346027945
8: 0.09804825608449834
9: 0.09645450435269572
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.10095392152650015
1: 0.10168439384451268
2: 0.09187991827033537
3: 0.09048957309145751
4: 0.10925520420279619
5: 0.09311212701115787
6: 0.09571162410668127
7: 0.11106420961956176
8: 0.09557615036348709
9: 0.11027287796351026
Prediction: 3, Ans: 2

Posterior (in log scale):
0: 0.12883715993917103
1: 0.06792200949976417
2: 0.10072550935945504
3: 0.09664388845567827
4: 0.10821578109385052
5: 0.0951558209973181
6: 0.10050293556004164
7: 0.10797680719344636
8: 0.0920068326170796
9: 0.10201325528419523
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.13142189141591468
1:

Posterior (in log scale):
0: 0.11299797386526111
1: 0.1184327922770847
2: 0.09866344438762116
3: 0.07727183287005535
4: 0.10048765635969568
5: 0.08906671263704329
6: 0.11085709518370437
7: 0.10716516149743553
8: 0.08632218861703703
9: 0.0987351423050618
Prediction: 3, Ans: 3

Posterior (in log scale):
0: 0.076697769047429
1: 0.13294790726792297
2: 0.09301135272803233
3: 0.10402530030604112
4: 0.1005992690396834
5: 0.09171473660484349
6: 0.09339155205539476
7: 0.10286369323261345
8: 0.09951809338382693
9: 0.10523032633421261
Prediction: 0, Ans: 0

Posterior (in log scale):
0: 0.10322120944413649
1: 0.1279058115699603
2: 0.1053486882183054
3: 0.09640904326247138
4: 0.09376904467864236
5: 0.09825475538142416
6: 0.11050085687551431
7: 0.07400883304215206
8: 0.0999640619341331
9: 0.09061769559326034
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.06763070332123276
1: 0.1462784169744862
2: 0.09013784574234376
3: 0.09556420303601988
4: 0.10025142047322244
5: 0.08858833052948462
6: 0.094

Posterior (in log scale):
0: 0.11175565306499412
1: 0.1368105404811874
2: 0.09890195644365297
3: 0.10166242212851924
4: 0.08343258832298933
5: 0.09852341356032558
6: 0.1010977373663132
7: 0.09164719341386274
8: 0.09590213902362214
9: 0.08026635619453323
Prediction: 9, Ans: 9

Posterior (in log scale):
0: 0.10340137139624588
1: 0.11707865448940948
2: 0.09307343771783572
3: 0.10236668136049036
4: 0.09344783999381569
5: 0.09935505284460265
6: 0.0867402413184205
7: 0.10392550037998764
8: 0.10050783735347953
9: 0.10010338314571247
Prediction: 6, Ans: 6

Posterior (in log scale):
0: 0.07876493874730066
1: 0.13028938991507497
2: 0.09849589764292448
3: 0.0977679723847298
4: 0.09864734321655129
5: 0.0894980658294292
6: 0.10272359102301801
7: 0.10762736509362801
8: 0.09442401099468296
9: 0.10176142515266051
Prediction: 0, Ans: 0

Posterior (in log scale):
0: 0.10098538398089756
1: 0.1265672151657805
2: 0.10985288771524108
3: 0.09394076232451813
4: 0.09479948560016498
5: 0.08484031173013645
6: 0.

Posterior (in log scale):
0: 0.10210075782271368
1: 0.1314604190952406
2: 0.09358431341276414
3: 0.1025725726166599
4: 0.09411348283078513
5: 0.09514465827424888
6: 0.07585394896032743
7: 0.11157100920011166
8: 0.0951434785163537
9: 0.09845535927079498
Prediction: 6, Ans: 6

Posterior (in log scale):
0: 0.0942489586237295
1: 0.13149761425528522
2: 0.09000077202152386
3: 0.1007803982075554
4: 0.09624732862324342
5: 0.09235619585615143
6: 0.07690598844351679
7: 0.11818925484989257
8: 0.09404095952815814
9: 0.10573252959094366
Prediction: 6, Ans: 6

Posterior (in log scale):
0: 0.09263656742139668
1: 0.13181444297082529
2: 0.09449303609198816
3: 0.08507409526820742
4: 0.10570596184552253
5: 0.08368247215754152
6: 0.09270143434060556
7: 0.11730413254832173
8: 0.08938844458334165
9: 0.10719941277224945
Prediction: 5, Ans: 5

Posterior (in log scale):
0: 0.1115481935777835
1: 0.12704743924040013
2: 0.08962945969810719
3: 0.09863240558575535
4: 0.09133004595062279
5: 0.10249387501905055
6: 0.

...

Posterior (in log scale):
0: 0.11787674971825857
1: 0.0982585113545501
2: 0.10376569649848355
3: 0.10534394686668054
4: 0.09643608434811636
5: 0.09741485862572241
6: 0.11443718746087717
7: 0.0800801069847474
8: 0.09751118166367742
9: 0.08887567647888646
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.11683755852446369
1: 0.10543024783708778
2: 0.10620449966763193
3: 0.10674866781152581
4: 0.09463444525162987
5: 0.0967101528796488
6: 0.11366842194947077
7: 0.07639719251742402
8: 0.09783999566234092
9: 0.08552881789877655
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.12905485144223286
1: 0.0677485778815298
2: 0.09588874461514454
3: 0.09944818839303181
4: 0.10076972413300458
5: 0.09675791652974888
6: 0.11303729667126644
7: 0.10127679920717034
8: 0.09330727807682919
9: 0.10271062305004158
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.07671120203481298
1: 0.13183053133177433
2: 0.0967389824509254
3: 0.09503638912247664
4: 0.0995917359464884
5: 0.08756918294617108
6: 0.

Posterior (in log scale):
0: 0.10229041435437718
1: 0.12473141432983458
2: 0.0991020182943613
3: 0.11016268901388722
4: 0.08395750474496894
5: 0.0987124993279964
6: 0.0968013508016384
7: 0.09450360379498948
8: 0.09898341426661832
9: 0.09075509107132834
Prediction: 4, Ans: 4

Posterior (in log scale):
0: 0.10491016036612523
1: 0.12463674124917269
2: 0.10016563125396107
3: 0.11118893420150854
4: 0.08448454372336274
5: 0.09387945730936567
6: 0.10047877605330835
7: 0.09311492147148002
8: 0.0967596470308038
9: 0.09038118734091193
Prediction: 4, Ans: 4

Posterior (in log scale):
0: 0.10833857111163725
1: 0.12071356395735114
2: 0.10789828496732404
3: 0.10495335721079195
4: 0.09104520858408222
5: 0.0971029432061636
6: 0.1154193026532424
7: 0.07497495194959163
8: 0.0979504735626164
9: 0.08160334279719939
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.08262506217406299
1: 0.1245696659182737
2: 0.09903410073911675
3: 0.09318375367823352
4: 0.10435945805954261
5: 0.08823621210003472
6: 0.09

Posterior (in log scale):
0: 0.11877216008529068
1: 0.09641450252458789
2: 0.09821040530270883
3: 0.09447448331474258
4: 0.1024130930381008
5: 0.0964075678448227
6: 0.10173026783315325
7: 0.09870847688232703
8: 0.09382720831498131
9: 0.09904183485928499
Prediction: 8, Ans: 8

Posterior (in log scale):
0: 0.1158787473146088
1: 0.12490672062844758
2: 0.10248242630759023
3: 0.10691079044848288
4: 0.0806587615706504
5: 0.09844955018171482
6: 0.103937823885431
7: 0.08841311735252985
8: 0.09559355876436883
9: 0.08276850354617556
Prediction: 4, Ans: 4

Posterior (in log scale):
0: 0.11335624851639921
1: 0.11068306519692515
2: 0.0940861335448814
3: 0.10418972198428741
4: 0.09521976514570962
5: 0.09742652607402173
6: 0.08046702832953409
7: 0.10827160328109783
8: 0.09702643500634414
9: 0.09927347292079941
Prediction: 6, Ans: 6

Posterior (in log scale):
0: 0.08282722551398831
1: 0.12473644938340606
2: 0.09876405585315014
3: 0.09357747673517103
4: 0.10023937363870833
5: 0.08888844578987248
6: 0.1

Posterior (in log scale):
0: 0.10210835554892052
1: 0.1358518357583228
2: 0.10492249121356667
3: 0.1048707636604772
4: 0.08286975589938107
5: 0.09537465836484112
6: 0.10244909850958538
7: 0.09259397713096613
8: 0.09639648327804554
9: 0.08256258063589364
Prediction: 9, Ans: 9

Posterior (in log scale):
0: 0.07404688458765848
1: 0.14071044543785524
2: 0.09435994103116699
3: 0.09729392287734061
4: 0.09940840147471103
5: 0.08804756480514206
6: 0.09904685252722438
7: 0.1113904069208961
8: 0.08960356416349587
9: 0.10609201617450928
Prediction: 0, Ans: 0

Posterior (in log scale):
0: 0.13002542550832213
1: 0.06344515643507995
2: 0.0937035492725488
3: 0.09898883963435332
4: 0.10853973220979046
5: 0.09748921555960287
6: 0.1011506468405526
7: 0.10905201449199108
8: 0.09189711086925209
9: 0.10570830917850663
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.10493957326177498
1: 0.1198597562700186
2: 0.07461972607648397
3: 0.08828634278884283
4: 0.10603179688896115
5: 0.09656347055339165
6: 0.

0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 

5:
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0

In [26]:
NB_main(1, train_image,train_label,test_image,test_label)

Posterior (in log scale):
0: 0.10390092610661601
1: 0.14268657193793427
2: 0.10763848368900857
3: 0.0920215867810484
4: 0.09137764590103925
5: 0.09325322015955205
6: 0.12007041175371351
7: 0.07691590401273901
8: 0.09223761175455686
9: 0.07989763790379208
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.08531371419378267
1: 0.12522776833059018
2: 0.06442891843554288
3: 0.08220233900388071
4: 0.10683333249577863
5: 0.08981045758706167
6: 0.08158381921721762
7: 0.144520096950411
8: 0.09338197248985337
9: 0.12669758129588127
Prediction: 2, Ans: 2

Posterior (in log scale):
0: 0.10886024237442053
1: 0.07584017380509671
2: 0.10166795949903897
3: 0.09972803725924329
4: 0.10008608644151523
5: 0.1008167354162278
6: 0.09924988943676655
7: 0.11155085962667924
8: 0.09869995723839742
9: 0.10350005890261427
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.07642611546815506
1: 0.21536571554802877
2: 0.08574904554750223
3: 0.084375500631421
4: 0.08773632935725195
5: 0.08406593819131213
6: 0.

Posterior (in log scale):
0: 0.07093220018604339
1: 0.22083882605837413
2: 0.0862689109389884
3: 0.10534942306376667
4: 0.07404814079220526
5: 0.07651241000970202
6: 0.08299282419571877
7: 0.1054062365987898
8: 0.07708153181023489
9: 0.10056949634617661
Prediction: 0, Ans: 4

Posterior (in log scale):
0: 0.10527025190437668
1: 0.12694343161926824
2: 0.10368737131113209
3: 0.08891141584878635
4: 0.09175987891220447
5: 0.09052518648183858
6: 0.13200368380316138
7: 0.08392121335751014
8: 0.08745486806629903
9: 0.08952269869542287
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.07352806556460648
1: 0.14571581576131773
2: 0.07354845663642655
3: 0.07513409244899304
4: 0.10414606199879782
5: 0.07646601374842087
6: 0.1018702237352905
7: 0.14628626936240036
8: 0.07464242769096753
9: 0.12866257305277898
Prediction: 0, Ans: 2

Posterior (in log scale):
0: 0.10357113005570262
1: 0.1582993827106674
2: 0.1041685290377541
3: 0.09009014577180119
4: 0.08381536269069093
5: 0.09508260560465315
6: 0

Posterior (in log scale):
0: 0.11319190095471733
1: 0.07647465527556802
2: 0.10393664228963778
3: 0.09959939596712142
4: 0.10074859934665342
5: 0.10034983368310425
6: 0.10937737924016795
7: 0.10204242099718744
8: 0.09799634484322531
9: 0.09628282740261704
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.11520792629569446
1: 0.13998347029200034
2: 0.10214838429959877
3: 0.09003503569342418
4: 0.08711610880761296
5: 0.09428874621171586
6: 0.11867691260485584
7: 0.07814225664060671
8: 0.09242219127741273
9: 0.08197896787707827
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.09609237928828164
1: 0.1040414348134073
2: 0.09639516147213247
3: 0.08986836786923556
4: 0.09918226850780278
5: 0.09297625630767374
6: 0.1046803788498153
7: 0.11903183091046743
8: 0.0918201033348839
9: 0.10591181864629978
Prediction: 3, Ans: 3

Posterior (in log scale):
0: 0.09433681734494388
1: 0.14853253237945607
2: 0.0871108845330054
3: 0.10066525459267348
4: 0.09191883745170822
5: 0.09164485047870467
6: 

Posterior (in log scale):
0: 0.09712335926925433
1: 0.0833595330521877
2: 0.09134354577752503
3: 0.08822369498150538
4: 0.10174313649698132
5: 0.0899578135366924
6: 0.1086081197154737
7: 0.13839771260723538
8: 0.08640808051968171
9: 0.11483500404346313
Prediction: 1, Ans: 8

Posterior (in log scale):
0: 0.11715449801473815
1: 0.08087664901523596
2: 0.10727717551649228
3: 0.0969763264827229
4: 0.09716699085782352
5: 0.09822757131539986
6: 0.12233980578884932
7: 0.09307513752396186
8: 0.09492198246173145
9: 0.09198386302304472
Prediction: 1, Ans: 7

Posterior (in log scale):
0: 0.10255290433080365
1: 0.08799673628388612
2: 0.10390992331917247
3: 0.09438027631432667
4: 0.09845262699239742
5: 0.09674895895172159
6: 0.11455978781272465
7: 0.1047782118563115
8: 0.0953638831292789
9: 0.10125669100937694
Prediction: 1, Ans: 3

Posterior (in log scale):
0: 0.11246446927195444
1: 0.13443871146357356
2: 0.10594757114157972
3: 0.09618735577649236
4: 0.08922132527413977
5: 0.09492216191533896
6: 0.

Posterior (in log scale):
0: 0.10812327645678205
1: 0.1395176834183672
2: 0.10308825788611843
3: 0.09205176882142627
4: 0.09099950684818049
5: 0.09938024794296424
6: 0.1173880878685234
7: 0.06712494342653963
8: 0.09502929600266861
9: 0.08729693132842983
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.09381966186517936
1: 0.1578831784047611
2: 0.08777754109710727
3: 0.07990215085731947
4: 0.08490800595352867
5: 0.08543252610132622
6: 0.12298717945861931
7: 0.09761305980876364
8: 0.08328260041146975
9: 0.10639409604192543
Prediction: 3, Ans: 3

Posterior (in log scale):
0: 0.11104790313344903
1: 0.07584753407095761
2: 0.10215597995687338
3: 0.10024893945839078
4: 0.10156619174507898
5: 0.10118938994497129
6: 0.0990589578554789
7: 0.10784392818455946
8: 0.09873337939349157
9: 0.10230779625674896
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.10973576236737419
1: 0.13965957004902196
2: 0.10384934076099869
3: 0.09435380187341962
4: 0.09094905077967647
5: 0.0938743364641778
6: 0

...

Posterior (in log scale):
0: 0.1015824207488553
1: 0.14685996581424077
2: 0.10151050255396502
3: 0.0945555806119995
4: 0.09112978226447238
5: 0.0931208062938924
6: 0.11024114387814808
7: 0.08433392597789241
8: 0.0932334557861782
9: 0.08343241607035583
Prediction: 9, Ans: 9

Posterior (in log scale):
0: 0.10432992407926799
1: 0.08414168459239922
2: 0.0990022938987152
3: 0.09735180843530226
4: 0.09611431467234742
5: 0.09642892017642526
6: 0.09624448777378394
7: 0.12262237804307531
8: 0.09463236849976552
9: 0.10913181982891795
Prediction: 1, Ans: 8

Posterior (in log scale):
0: 0.09968661915220423
1: 0.10513313788004923
2: 0.09715477309096802
3: 0.09274548988470438
4: 0.09544190254109686
5: 0.09251702718072571
6: 0.11967077829001274
7: 0.10911931585799993
8: 0.0889033659330619
9: 0.0996275901891771
Prediction: 8, Ans: 2

Posterior (in log scale):
0: 0.10812904699100138
1: 0.09725339750110328
2: 0.10943949110847338
3: 0.09888606513544164
4: 0.09754552357844108
5: 0.0988831593454459
6: 0.12

Posterior (in log scale):
0: 0.10049263032149774
1: 0.1507587548210428
2: 0.11150125093158963
3: 0.09859121071387875
4: 0.08692035542853878
5: 0.09171863100364364
6: 0.1190710966859514
7: 0.07353142215675554
8: 0.09310792689993998
9: 0.07430672103716174
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.08119072764210825
1: 0.15608053897530053
2: 0.08948239580672243
3: 0.08608868325429503
4: 0.09332955634303797
5: 0.08737215603974083
6: 0.09545793582186267
7: 0.11968448594151421
8: 0.08524963778093309
9: 0.10606388239448486
Prediction: 0, Ans: 0

Posterior (in log scale):
0: 0.11158410684434054
1: 0.07555612904040739
2: 0.10320988247035247
3: 0.09924413890473233
4: 0.1003835697648579
5: 0.10033912917622899
6: 0.1133659925455534
7: 0.10230845533570863
8: 0.0975024846826484
9: 0.09650611123516993
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.09823025500228358
1: 0.18219108192460487
2: 0.09945646929030874
3: 0.09116730241748712
4: 0.08339524210993464
5: 0.08866606881532516
6: 0

Posterior (in log scale):
0: 0.06528081879200867
1: 0.1845384145427776
2: 0.07575835204686338
3: 0.08216549286628523
4: 0.09653745825674569
5: 0.07582990904293371
6: 0.12027773531683439
7: 0.10529326667246197
8: 0.08776603321342988
9: 0.10655251924965961
Prediction: 0, Ans: 0

Posterior (in log scale):
0: 0.0999450870646206
1: 0.1549552092072254
2: 0.10764361850349959
3: 0.09223300783420761
4: 0.09027405812079257
5: 0.09145847781192191
6: 0.11625796145450587
7: 0.07742494458950089
8: 0.09134855776540031
9: 0.07845907764832531
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.06908213776777149
1: 0.17075316052663939
2: 0.07600331858251773
3: 0.07869267572400136
4: 0.09735891429821787
5: 0.07575107666420285
6: 0.10289854950138848
7: 0.13327676094654647
8: 0.07583524967586128
9: 0.12034815631285321
Prediction: 0, Ans: 0

Posterior (in log scale):
0: 0.08855804532776879
1: 0.10458966790954312
2: 0.08073953283263807
3: 0.07867494085408412
4: 0.10045415269706967
5: 0.08637101462266959
6:

Posterior (in log scale):
0: 0.09658444660995769
1: 0.19781638745494942
2: 0.09697911918284492
3: 0.08937700275726042
4: 0.08057331286978833
5: 0.08662869474482884
6: 0.10298525490460259
7: 0.084257105850871
8: 0.08691659672390885
9: 0.077882078900988
Prediction: 9, Ans: 9

Posterior (in log scale):
0: 0.061255726399577895
1: 0.22761402756203122
2: 0.0781066840827963
3: 0.09198471811937961
4: 0.08771769359115918
5: 0.07344633767385891
6: 0.09302654843271928
7: 0.11033157038220269
8: 0.06944324624631265
9: 0.1070734475099623
Prediction: 0, Ans: 0

Posterior (in log scale):
0: 0.11241906933525446
1: 0.07413484644256454
2: 0.09945957662221576
3: 0.09873514559025987
4: 0.10113393937532698
5: 0.09958064649636172
6: 0.0981445640162875
7: 0.11537097033708929
8: 0.0960550109643859
9: 0.104966230820254
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.08813289000173417
1: 0.1539448486363022
2: 0.07549193820601797
3: 0.07890148632551447
4: 0.09563274661324267
5: 0.08100162912520285
6: 0.0962

0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 1 1 0 0 0 0 0 0 1 1 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 1 1 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 1 1 1 1 0 0 0 1 1 1 1 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0

# Online learning

In [27]:
def Binomial_Beta(a, b):
    f = open('testfile.txt')
    line = f.readline()
    num = 1
    while line:
        one = line.count('1')
        zero = line.count('0')
        total = one + zero
        one_prob = one/total
        zero_prob = zero/total
        # calcuate !
        likelihood = math.factorial(total)/math.factorial(one)/math.factorial(zero)*one_prob**one*zero_prob**zero
        print('case {}: {}'.format(num,line),end='')
        print('Likelihood: {}'.format(likelihood))
        print('Beta prior:     a={} b={}'.format(a,b))
        a+=one
        b+=zero
        print('Beta posterior: a={} b={}'.format(a,b))
        print()
        line=f.readline()
        num+=1

In [28]:
Binomial_Beta(0, 0)

case 1: 0101010101001011010101
Likelihood: 0.16818809509277344
Beta prior:     a=0 b=0
Beta posterior: a=11 b=11

case 2: 0110101
Likelihood: 0.29375515303997474
Beta prior:     a=11 b=11
Beta posterior: a=15 b=14

case 3: 010110101101
Likelihood: 0.22860542417943364
Beta prior:     a=15 b=14
Beta posterior: a=22 b=19

case 4: 0101101011101011010
Likelihood: 0.18286870706509092
Beta prior:     a=22 b=19
Beta posterior: a=33 b=27

case 5: 111101100011110
Likelihood: 0.21430705488578314
Beta prior:     a=33 b=27
Beta posterior: a=43 b=32

case 6: 101110111000110
Likelihood: 0.20659760529408
Beta prior:     a=43 b=32
Beta posterior: a=52 b=38

case 7: 1010010111
Likelihood: 0.25082265600000003
Beta prior:     a=52 b=38
Beta posterior: a=58 b=42

case 8: 11101110110
Likelihood: 0.2619678932864457
Beta prior:     a=58 b=42
Beta posterior: a=66 b=45

case 9: 01000111101
Likelihood: 0.2360912887150679
Beta prior:     a=66 b=45
Beta posterior: a=72 b=50

case 10: 110100111
Likelihood: 0.273129

In [29]:
Binomial_Beta(10, 0)

case 1: 0101010101001011010101
Likelihood: 0.16818809509277344
Beta prior:     a=10 b=0
Beta posterior: a=21 b=11

case 2: 0110101
Likelihood: 0.29375515303997474
Beta prior:     a=21 b=11
Beta posterior: a=25 b=14

case 3: 010110101101
Likelihood: 0.22860542417943364
Beta prior:     a=25 b=14
Beta posterior: a=32 b=19

case 4: 0101101011101011010
Likelihood: 0.18286870706509092
Beta prior:     a=32 b=19
Beta posterior: a=43 b=27

case 5: 111101100011110
Likelihood: 0.21430705488578314
Beta prior:     a=43 b=27
Beta posterior: a=53 b=32

case 6: 101110111000110
Likelihood: 0.20659760529408
Beta prior:     a=53 b=32
Beta posterior: a=62 b=38

case 7: 1010010111
Likelihood: 0.25082265600000003
Beta prior:     a=62 b=38
Beta posterior: a=68 b=42

case 8: 11101110110
Likelihood: 0.2619678932864457
Beta prior:     a=68 b=42
Beta posterior: a=76 b=45

case 9: 01000111101
Likelihood: 0.2360912887150679
Beta prior:     a=76 b=45
Beta posterior: a=82 b=50

case 10: 110100111
Likelihood: 0.27312

MLE:
    
https://towardsdatascience.com/maximum-likelihood-estimation-explained-normal-distribution-6207b322e47f